In [ ]:
#! pip install git+https://github.com/openai/whisper.git -q

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done


In [ ]:
!pip install openai-whisper==20230117

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
import sys
import subprocess
import numpy as np
import os
from moviepy.editor import *

In [ ]:
import whisper

model = whisper.load_model("medium")

In [ ]:
model.device

device(type='cuda', index=0)

In [ ]:
from IPython.display import Audio
Audio("/content/drive/MyDrive/Speechify/مرحبًا مرحبًا بكم في مشروعنا المسمى Spee.mp3")

In [ ]:
# load audio and pad/trim it to fit 30 seconds
audio = whisper.load_audio("/content/drive/MyDrive/Speechify/مرحبًا مرحبًا بكم في مشروعنا المسمى Spee.mp3")
audio = whisper.pad_or_trim(audio)


# Convert audio to float32 if necessary
if audio.dtype != 'float32':
    audio = audio.astype('float32')

# make log-Mel spectrogram and move to the same device as the model
mel = whisper.log_mel_spectrogram(audio).to(model.device)

# detect the spoken language
_, probs = model.detect_language(mel)
print(f"Detected language: {max(probs, key=probs.get)}")

# decode the audio
options = whisper.DecodingOptions()
result = whisper.decode(model, mel, options)

# print the recognized text
print(result.text)

Detected language: ar
مرحباً بكم في مشروعنا المسمى Spichify


In [ ]:
input_video = '/content/drive/MyDrive/Speechify/speechify_welcome.mp4'

In [ ]:
from IPython.display import HTML
from base64 import b64encode
mp4 = open(input_video,'rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=400 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)

In [ ]:
from whisper.utils import write_vtt

In [ ]:
output_dir = '/content/'
filename = "speechify_welcome"

transcript = [
    {
        "start": 0.0,
        "end": 0.04,
        "text": result.text
    }
]
with open(os.path.join(output_dir, filename + ".vtt"), "w") as vtt:
    write_vtt(transcript, file=vtt)

In [ ]:
from moviepy.editor import *

# Load the video and audio files
video = VideoFileClip('/content/drive/MyDrive/Speechify/speechify_welcome.mp4')
audio = AudioFileClip('/content/drive/MyDrive/Speechify/مرحبًا مرحبًا بكم في مشروعنا المسمى Spee.mp3')

# Add the audio to the video
result = video.set_audio(audio)

# Write the result to a new video file
result.write_videofile('result.mp4', fps=video.fps)

Moviepy - Building video result.mp4.
MoviePy - Writing audio in resultTEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video result.mp4



Moviepy - Done !
Moviepy - video ready result.mp4


In [ ]:

import gradio as gr 
import os
import sys
import subprocess
#from moviepy.editor import VideoFileClip

import whisper
from whisper.utils import write_vtt

model = whisper.load_model("medium")

def video2mp3(video_file, output_ext="mp3"):
    filename, ext = os.path.splitext(video_file)
    subprocess.call(["ffmpeg", "-y", "-i", video_file, f"{filename}.{output_ext}"], 
                    stdout=subprocess.DEVNULL,
                    stderr=subprocess.STDOUT)
    return f"{filename}.{output_ext}"


def translate(input_video):

    audio_file = video2mp3(input_video)
    
    options = dict(beam_size=5, best_of=5)
    translate_options = dict(task="translate", **options)
    result = model.transcribe(audio_file,**translate_options)

    output_dir = '/content/'
    audio_path = audio_file.split(".")[0]

    with open(os.path.join(output_dir, audio_path + ".vtt"), "w") as vtt:
      write_vtt(result["segments"], file=vtt)

    subtitle = audio_path + ".vtt"
    output_video = audio_path + "_subtitled.mp4"

    os.system(f"ffmpeg -i {input_video} -vf subtitles={subtitle} {output_video}")

    return output_video



title = "Add Text/Caption to your YouTube Shorts - MultiLingual"

block = gr.Blocks()

with block:

    with gr.Group():
        with gr.Box(): 

           

            with gr.Row().style():
               
                inp_video = gr.Video(
                    label="Input Video",
                    type="filepath",
                    mirror_webcam = False
                )
                op_video = gr.Video()
            btn = gr.Button("Generate Subtitle Video")
        
        
        


        
        btn.click(translate, inputs=[inp_video], outputs=[op_video])
 
        gr.HTML('''
        <div class="footer">
                    <p>Model by <a href="https://github.com/openai/whisper" style="text-decoration: underline;" target="_blank">OpenAI</a> - Gradio App by <a href="https://twitter.com/1littlecoder" style="text-decoration: underline;" target="_blank">1littlecoder</a>
                    </p>
        </div>
        ''')

block.launch(debug = True)
